# Wholesale Customers

Description:
* 440 rows, 2 parent and 6 child features

Parent features:
* Channel, Region

Child features:
* Fresh, Milk, Grocery, Frozen, Detergents_Paper, Delicassen

Source: https://www.kaggle.com/binovi/wholesale-customers-data-set

In [1]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt

In [2]:
ws = pd.read_csv("../data/wholesale.csv")

In [3]:
parent = ws[['Channel', 'Region']]
parent.head()

Channel  Region
0        2       3
1        2       3
2        2       3
3        1       3
4        2       3

In [4]:
child = ws[['Fresh', 'Milk', 'Grocery', 'Frozen', 'Detergents_Paper', 'Delicassen']]
child.head()

Fresh  Milk  Grocery  Frozen  Detergents_Paper  Delicassen
0  12669  9656     7561     214              2674        1338
1   7057  9810     9568    1762              3293        1776
2   6353  8808     7684    2405              3516        7844
3  13265  1196     4221    6404               507        1788
4  22615  5410     7198    3915              1777        5185

In [5]:
import sys
sys.path.append("C:/Users/notes/grab")

X = parent.values.astype(np.float32)
y = child.values.astype(np.float32)

# Model Evaluation

In [6]:
from model.gmm import GMM
from model.cgan import CGAN
from model.bayesnn import BayesNN
from model.mcdropout import MCDropout
from model.deepensemble import DeepEnsemble
from hyperopt.hyperopt import (hyperopt,
                               hyperopt_log,
                               hyperparam_plot,
                               performance_plot)
from visualisation.visualisation import (plot_surface,
                                         plot_prob_fixed,
                                         plot_violin,
                                         plot_prob_violin,
                                         plot_binned_violin)
from data.synthetic import plot_data

[INFO 07-14 16:48:20] ipy_plotting: Injecting Plotly library into cell. Do not overwrite or delete cell.


# Model: Gaussian Mixture Density Network

In [11]:
params = {
    "x_features": 2,
    "y_features": 6,
    "epochs": 20000,
}
opt_params = {
    'n_components': [1,100],
    'n_hidden': [1,100],
}

gmm, best_params, best_vals, experiment, exp_model = hyperopt(
    GMM,
    params,
    opt_params,
    X, y,
    trials=30,
    val_split=0.8)

y_hat = gmm.predict(X)

[INFO 07-14 11:47:07] ax.modelbridge.dispatch_utils: Using Bayesian Optimization generation strategy: GenerationStrategy(name='Sobol+GPEI', steps=[Sobol for 5 trials, GPEI for subsequent trials]). Iterations after 5 will take longer to generate due to  model-fitting.
[INFO 07-14 11:47:07] ax.service.managed_loop: Started full optimization with 30 steps.
[INFO 07-14 11:47:07] ax.service.managed_loop: Running optimization trial 1...
[INFO 07-14 11:49:26] ax.service.managed_loop: Running optimization trial 2...
[INFO 07-14 11:52:01] ax.service.managed_loop: Running optimization trial 3...
[INFO 07-14 11:54:12] ax.service.managed_loop: Running optimization trial 4...
[INFO 07-14 11:56:45] ax.service.managed_loop: Running optimization trial 5...
[INFO 07-14 11:59:07] ax.service.managed_loop: Running optimization trial 6...
[INFO 07-14 12:00:54] ax.service.managed_loop: Running optimization trial 7...
[INFO 07-14 12:03:30] ax.service.managed_loop: Running optimization trial 8...
[INFO 07-14 

In [12]:
print(f"n_components: {gmm.n_components}")
print(f"n_hidden: {gmm.n_hidden}")
display(hyperopt_log(experiment))
hyperparam_plot(exp_model, "n_components", "n_hidden")

n_components: 62
n_hidden: 100


n_components  n_hidden        loss       fKL       rKL        JS
0             63        55   65.139488  0.000000  0.000000  0.000000
1             75        52   62.665951  4.510324 -0.025694  0.272713
2             43        96   61.241211  3.921921 -0.036943  0.262059
3             69        49   62.923107  4.164258 -0.022490  0.245293
4             76        33   63.899952  4.142752 -0.017146  0.243479
5             23       100   62.150425  4.402960 -0.035300  0.267109
6             62       100   60.537842  3.921921 -0.036943  0.262059
7             87        98   62.158886  3.491855 -0.045091  0.256272
8             63        93   61.537746  3.135415 -0.067957  0.245100
9            100        48   64.708626  4.125810 -0.015571  0.241822
10            54       100   60.557438  3.095790 -0.072165  0.242583
11             1         1  767.628723  2.835582 -0.054011  0.218953
12           100         9   61.075333  2.997065 -0.051504  0.225662
13           100        26   63.300747  4.233532 -0.029299  0.251806
14           100       100   63.086502  3.723817 -0.044352  0.262672
15            34       100   61.781948  3.989661 -0.031546  0.265146
16           100        79   62.704678  4.116744 -0.009923  0.241421
17             1       100   64.761185  4.118319 -0.013074  0.241228
18            91        18   61.703945  0.390043 -0.016039  0.031018
19            86        36   64.289963  0.000000  0.000000  0.000000
20           100         1  348.869049  2.725224 -0.060561  0.215306
21             1        75   63.805191  3.396747 -0.040115  0.237139
22           100        13   61.203751  2.793218 -0.072206  0.221529
23           100        67   62.682266  3.989661 -0.031546  0.265146
24             1        38   61.668949  3.028157 -0.079755  0.243929
25             1        85   65.556175  0.000000  0.000000  0.000000
26             1        64   63.445560  4.125810 -0.015571  0.241822
27             1        28   61.465176  2.978710 -0.050232  0.223881
28            52        71   62.123592  3.674420 -0.028231  0.240768
29            54        25   61.404751  4.066425 -0.040851  0.272253

In [13]:
from performance.performance import prob_overlap, kl, js
p, q = prob_overlap(y, y_hat, bins=5)
print("fKL:", kl(p, q))
print("rKL:", kl(q, p))
print("JS:", js(p, q))

fKL: 4.014093593508826
rKL: -0.03561775113966589
JS: 0.2673970711051785


# Model: Conditional Generative Adversarial Network

In [14]:
params = {
    "x_features": 2,
    "y_features": 6,
    "epochs": 20000,
}
opt_params = {
    'latent_dim': [1,100],
    'g_hidden': [1,100],
    'd_hidden': [1,100],
    'label_smooth': [0.0,1.0],
    'd_dropout': [0.0, 0.9],
    'gp_weight': [0.0, 1.0],
    'ds_weight': [0.0, 1.0],
}

cgan, best_params, best_vals, experiment, exp_model = hyperopt(
    CGAN,
    params,
    opt_params,
    X, y,
    trials=30,
    val_split=0.8)

y_hat = cgan.predict(X)

[INFO 07-14 13:00:42] ax.modelbridge.dispatch_utils: Using Bayesian Optimization generation strategy: GenerationStrategy(name='Sobol+GPEI', steps=[Sobol for 7 trials, GPEI for subsequent trials]). Iterations after 7 will take longer to generate due to  model-fitting.
[INFO 07-14 13:00:42] ax.service.managed_loop: Started full optimization with 30 steps.
[INFO 07-14 13:00:42] ax.service.managed_loop: Running optimization trial 1...
[INFO 07-14 13:03:26] ax.service.managed_loop: Running optimization trial 2...
[INFO 07-14 13:05:36] ax.service.managed_loop: Running optimization trial 3...
[INFO 07-14 13:07:37] ax.service.managed_loop: Running optimization trial 4...
[INFO 07-14 13:09:35] ax.service.managed_loop: Running optimization trial 5...
[INFO 07-14 13:11:28] ax.service.managed_loop: Running optimization trial 6...
[INFO 07-14 13:13:24] ax.service.managed_loop: Running optimization trial 7...
[INFO 07-14 13:15:47] ax.service.managed_loop: Running optimization trial 8...
[INFO 07-14 

In [15]:
print(f"latent_dim: {cgan.latent_dim}")
print(f"g_hidden: {cgan.g_hidden}")
print(f"d_hidden: {cgan.d_hidden}")
print(f"label_smooth: {cgan.label_smooth}")
print(f"d_dropout: {cgan.d_dropout}")
print(f"gp_weight: {cgan.gp_weight}")
print(f"ds_weight: {cgan.ds_weight}")

display(hyperopt_log(experiment))
hyperparam_plot(exp_model, "g_hidden", "d_hidden")
hyperparam_plot(exp_model, "label_smooth", "d_dropout")
hyperparam_plot(exp_model, "gp_weight", "ds_weight")

latent_dim: 2
g_hidden: 4
d_hidden: 40
label_smooth: 0.9999999999963958
d_dropout: 3.389284325254425e-14
gp_weight: 3.8787660511321626e-15
ds_weight: 0.39026040001931134


latent_dim  g_hidden  d_hidden  label_smooth     d_dropout     gp_weight  \
0           62        84        62      0.793271  5.896898e-01  4.816962e-01   
1           76        27        30      0.485535  7.755827e-01  2.272085e-01   
2            5         2        52      0.242258  1.309314e-01  1.869001e-01   
3           27        40         7      0.850729  6.627433e-01  6.591369e-01   
4           52        30         3      0.726970  2.095228e-01  8.880083e-02   
5           81        62        34      0.769303  7.881851e-01  1.322819e-01   
6           26        86        99      0.889887  7.627827e-01  1.474131e-01   
7           14         3        37      0.330171  1.679383e-01  2.001760e-01   
8           18         3        30      0.368644  1.823384e-01  2.065503e-01   
9           16         1        18      0.390985  2.011886e-01  2.334965e-01   
10          24         4        33      0.389345  1.777211e-01  1.895514e-01   
11          29        11        35      0.355749  1.915181e-01  1.541172e-01   
12          23         5        31      0.459828  2.037938e-01  2.271446e-01   
13          23         5        35      0.553699  2.171414e-01  2.463382e-01   
14          24         4        40      0.610707  2.132287e-01  2.497177e-01   
15          18         3        41      0.659710  2.578580e-01  2.564313e-01   
16          29         4        42      0.630379  1.678757e-01  2.649015e-01   
17          28         3        43      0.597495  2.380792e-01  2.128430e-01   
18          24         4        42      0.625052  1.724965e-01  2.161302e-01   
19          20         4        42      0.637630  1.379283e-01  1.862244e-01   
20          21         3        44      0.621947  1.053847e-01  1.668440e-01   
21          15         4        41      0.667459  1.314625e-01  1.585529e-01   
22          13         4        40      0.704700  1.170368e-01  1.301855e-01   
23          10         4        38      0.768627  9.759592e-02  1.116718e-01   
24           8         4        36      0.833451  7.097973e-02  9.279096e-02   
25           5         4        37      0.913904  1.882543e-02  5.920664e-02   
26           3         4        39      0.988679  0.000000e+00  1.808050e-02   
27           2         4        40      1.000000  3.389284e-14  3.878766e-15   
28          53        95        36      0.744940  7.646293e-01  9.905165e-01   
29          83       100        45      0.942917  4.772833e-01  5.023631e-02   

    ds_weight          loss       fKL       rKL        JS  
0    0.526346  8.268245e+04 -0.239258  0.334202  0.011813  
1    0.243483  1.124974e+04 -0.239258  0.334202  0.011813  
2    0.327056 -6.560642e+04 -0.239258  0.334202  0.011813  
3    0.654287 -5.294783e+03 -0.239258  0.334202  0.011813  
4    0.883496 -8.433514e+03  0.000000  0.000000  0.000000  
5    0.270378  4.374040e+04 -0.239258  0.334202  0.011813  
6    0.659016  1.205969e+05 -0.239258  0.334202  0.011813  
7    0.425906 -2.540861e+05 -0.239258  0.334202  0.011813  
8    0.472723 -3.071337e+05 -0.239258  0.334202  0.011813  
9    0.446240 -7.678458e+04 -0.239258  0.334202  0.011813  
10   0.549062 -3.913962e+05 -0.239258  0.334202  0.011813  
11   0.579742  3.504568e+04 -0.239258  0.334202  0.011813  
12   0.530095 -4.459452e+05 -0.239258  0.334202  0.011813  
13   0.539158 -6.433599e+05 -0.239258  0.334202  0.011813  
14   0.561887 -7.468407e+05 -0.239258  0.334202  0.011813  
15   0.600341 -6.003718e+05 -0.239258  0.334202  0.011813  
16   0.513142 -6.918004e+05 -0.239258  0.334202  0.011813  
17   0.551160 -6.855869e+05 -0.239258  0.334202  0.011813  
18   0.597746 -9.546240e+05 -0.239258  0.334202  0.011813  
19   0.636681 -1.079092e+06 -0.239258  0.334202  0.011813  
20   0.695520 -8.273796e+05 -0.239258  0.334202  0.011813  
21   0.593808 -1.277717e+06 -0.239258  0.334202  0.011813  
22   0.560468 -1.826564e+06 -0.239258  0.334202  0.011813  
23   0.509288 -2.550200e+06 -0.239258  0.334202  0.011813  
24   0.461901 -3.536176

In [16]:
from performance.performance import prob_overlap, kl, js
p, q = prob_overlap(y, y_hat, bins=5)
print("fKL:", kl(p, q))
print("rKL:", kl(q, p))
print("JS:", js(p, q))

fKL: -0.23925831306205053
rKL: 0.33420208808667373
JS: 0.011813047399130097


# Model: Bayesian Neural Network

In [17]:
from model.bayesnn import BayesNN
from hyperopt.hyperopt import hyperopt
from hyperopt.hyperopt import hyperopt_log, hyperparam_plot, performance_plot

params = {
    "x_features": 2,
    "y_features": 6,
    "epochs": 2000,
}
opt_params = {
    'n_hidden': [1,100],
    'n_layers': [1,10],
}

bayesnn, best_params, best_vals, experiment, exp_model = hyperopt(
    BayesNN,
    params,
    opt_params,
    X, y,
    trials=30,
    val_split=0.8)

y_hat = bayesnn.predict(X)

[INFO 07-14 13:59:59] ax.modelbridge.dispatch_utils: Using Bayesian Optimization generation strategy: GenerationStrategy(name='Sobol+GPEI', steps=[Sobol for 5 trials, GPEI for subsequent trials]). Iterations after 5 will take longer to generate due to  model-fitting.
[INFO 07-14 13:59:59] ax.service.managed_loop: Started full optimization with 30 steps.
[INFO 07-14 13:59:59] ax.service.managed_loop: Running optimization trial 1...


Instructions for updating:
Please use `layer.add_weight` method instead.


[INFO 07-14 14:01:12] ax.service.managed_loop: Running optimization trial 2...
[INFO 07-14 14:02:00] ax.service.managed_loop: Running optimization trial 3...
[INFO 07-14 14:02:31] ax.service.managed_loop: Running optimization trial 4...
[INFO 07-14 14:03:37] ax.service.managed_loop: Running optimization trial 5...
[INFO 07-14 14:04:05] ax.service.managed_loop: Running optimization trial 6...
[INFO 07-14 14:04:54] ax.service.managed_loop: Running optimization trial 7...
[INFO 07-14 14:05:27] ax.service.managed_loop: Running optimization trial 8...
[INFO 07-14 14:05:50] ax.service.managed_loop: Running optimization trial 9...
[INFO 07-14 14:06:29] ax.service.managed_loop: Running optimization trial 10...
[INFO 07-14 14:07:20] ax.service.managed_loop: Running optimization trial 11...
[INFO 07-14 14:08:35] ax.service.managed_loop: Running optimization trial 12...
[INFO 07-14 14:09:14] ax.service.managed_loop: Running optimization trial 13...
[INFO 07-14 14:10:14] ax.service.managed_loop: R

In [18]:
print(f"n_hidden: {bayesnn.n_hidden}")
print(f"n_layers: {bayesnn.n_layers}")

display(hyperopt_log(experiment))
hyperparam_plot(exp_model, "n_hidden", "n_layers")

n_hidden: 61
n_layers: 5


n_hidden  n_layers         loss       fKL       rKL        JS
0         56         9    60.759109  3.234706 -0.085358  0.255161
1         61         5    59.736874  1.862326 -0.198931  0.173029
2         20         3    59.804321  0.667711 -0.268266  0.047987
3         68         7    61.081116  0.367572 -0.008548  0.029234
4         61         2    83.191399 -0.131688  0.160056  0.003541
5         31         6    60.204319  2.084882 -0.203535  0.192667
6          1         4   945.038452 -0.036961  0.289246  0.028683
7         32         1  4588.326172 -0.239258  0.334202  0.011813
8         61         3    59.971878  2.178174 -0.187767  0.199255
9         20         7    60.030895  2.669380 -0.122293  0.225893
10        36        10    60.726986  2.635929 -0.069935  0.212205
11        16         4    59.928967  1.380556 -0.220564  0.126228
12        29         8    60.704750  3.588339 -0.057394  0.254913
13        74         2    68.956268  0.035343 -0.016562  0.002266
14        34         4    59.915218  1.909605 -0.187923  0.178846
15       100         6    60.152279  2.578261 -0.139110  0.225390
16       100         8    61.693027  3.653031 -0.061273  0.260377
17        94        10    60.712826  3.133401 -0.100219  0.252151
18         1         9    77.569565 -0.110842  0.134819  0.002986
19        26         3    60.061581  1.758072 -0.179829  0.167280
20       100         4    60.115067  2.794172 -0.138612  0.238240
21        86         5    59.851173  3.414460 -0.074293  0.253299
22        68        10    61.312965  3.202623 -0.048999  0.233953
23        65         2    69.536530  0.244696 -0.024741  0.022570
24        61         2    72.905876  0.257903  0.030513  0.026463
25       100         3    59.871681  1.909099 -0.196966  0.176548
26        60         2    76.724396 -0.000485  0.003700  0.000394
27        51         2    96.561058 -0.195653  0.257144  0.007663
28        54         2    82.350952 -0.116608  0.142780  0.003260
29        53         2    86.994232  0.227275  0.177605  0.034871

[ERROR 07-14 14:35:47] PlotHelper: Have observations of arms with different features but same name. Arbitrary one will be plotted.


In [19]:
from performance.performance import prob_overlap, kl, js
p, q = prob_overlap(y, y_hat, bins=5)
print("fKL:", kl(p, q))
print("rKL:", kl(q, p))
print("JS:", js(p, q))

fKL: 1.924117868197028
rKL: -0.23960825104506464
JS: 0.17695382088352002


# Model: Monte Carlo Dropout

In [7]:
from model.mcdropout import MCDropout
from hyperopt.hyperopt import hyperopt
from hyperopt.hyperopt import hyperopt_log, hyperparam_plot, performance_plot

params = {
    "x_features": 2,
    "y_features": 6,
    "epochs": 2000,
}
opt_params = {
    'n_hidden': [1,100],
    'dropout': [0.1,0.9],
}

mcdropout, best_params, best_vals, experiment, exp_model = hyperopt(
    MCDropout,
    params,
    opt_params,
    X, y,
    trials=30,
    val_split=0.8)

y_hat, y_std = mcdropout.predict(X, return_std=True)
y_hat = mcdropout.predict(X)

[INFO 07-14 16:48:23] ax.modelbridge.dispatch_utils: Using Bayesian Optimization generation strategy: GenerationStrategy(name='Sobol+GPEI', steps=[Sobol for 5 trials, GPEI for subsequent trials]). Iterations after 5 will take longer to generate due to  model-fitting.
[INFO 07-14 16:48:23] ax.service.managed_loop: Started full optimization with 30 steps.
[INFO 07-14 16:48:23] ax.service.managed_loop: Running optimization trial 1...
[INFO 07-14 16:48:50] ax.service.managed_loop: Running optimization trial 2...
[INFO 07-14 16:49:19] ax.service.managed_loop: Running optimization trial 3...
[INFO 07-14 16:49:46] ax.service.managed_loop: Running optimization trial 4...
[INFO 07-14 16:50:15] ax.service.managed_loop: Running optimization trial 5...
[INFO 07-14 16:50:41] ax.service.managed_loop: Running optimization trial 6...
[INFO 07-14 16:51:12] ax.service.managed_loop: Running optimization trial 7...
[INFO 07-14 16:51:36] ax.service.managed_loop: Running optimization trial 8...
[INFO 07-14 

ValueError: Observation features not unique.Something went wrong constructing training data...

In [ ]:
print(f"n_hidden: {mcdropout.n_hidden}")
print(f"dropout: {mcdropout.dropout}")

display(hyperopt_log(experiment))
hyperparam_plot(exp_model, "n_hidden", "dropout")

In [ ]:
from performance.performance import prob_overlap, kl, js
p, q = prob_overlap(y, y_hat, bins=5)
print("fKL:", kl(p, q))
print("rKL:", kl(q, p))
print("JS:", js(p, q))

# Model: Deep Ensemble

In [21]:
from model.deepensemble import DeepEnsemble
from hyperopt.hyperopt import hyperopt
from hyperopt.hyperopt import hyperopt_log, hyperparam_plot, performance_plot

params = {
    "x_features": 2,
    "y_features": 6,
    "epochs": 2000,
}
opt_params = {
    'n_hidden': [1,100],
    'dropout': [0.1,0.5],
}

deepensemble, best_params, best_vals, experiment, exp_model = hyperopt(
    DeepEnsemble,
    params,
    opt_params,
    X, y,
    trials=30,
    val_split=0.8)

y_hat, y_std = deepensemble.predict(X, return_std=True)

[INFO 07-14 14:42:33] ax.modelbridge.dispatch_utils: Using Bayesian Optimization generation strategy: GenerationStrategy(name='Sobol+GPEI', steps=[Sobol for 5 trials, GPEI for subsequent trials]). Iterations after 5 will take longer to generate due to  model-fitting.
[INFO 07-14 14:42:33] ax.service.managed_loop: Started full optimization with 30 steps.
[INFO 07-14 14:42:33] ax.service.managed_loop: Running optimization trial 1...
[INFO 07-14 14:43:22] ax.service.managed_loop: Running optimization trial 2...
[INFO 07-14 14:44:11] ax.service.managed_loop: Running optimization trial 3...
[INFO 07-14 14:44:59] ax.service.managed_loop: Running optimization trial 4...
[INFO 07-14 14:45:53] ax.service.managed_loop: Running optimization trial 5...
[INFO 07-14 14:46:47] ax.service.managed_loop: Running optimization trial 6...
[INFO 07-14 14:46:47] StandardizeY: Outcome fKL is constant, within tolerance.
[INFO 07-14 14:46:47] StandardizeY: Outcome rKL is constant, within tolerance.
[INFO 07-14 

[INFO 07-14 15:07:06] ax.service.managed_loop: Running optimization trial 28...
[INFO 07-14 15:07:06] StandardizeY: Outcome fKL is constant, within tolerance.
[INFO 07-14 15:07:06] StandardizeY: Outcome rKL is constant, within tolerance.
[INFO 07-14 15:07:06] StandardizeY: Outcome JS is constant, within tolerance.
[INFO 07-14 15:08:12] ax.service.managed_loop: Running optimization trial 29...
[INFO 07-14 15:08:12] StandardizeY: Outcome fKL is constant, within tolerance.
[INFO 07-14 15:08:12] StandardizeY: Outcome rKL is constant, within tolerance.
[INFO 07-14 15:08:12] StandardizeY: Outcome JS is constant, within tolerance.
[INFO 07-14 15:09:02] ax.service.managed_loop: Running optimization trial 30...
[INFO 07-14 15:09:02] StandardizeY: Outcome fKL is constant, within tolerance.
[INFO 07-14 15:09:02] StandardizeY: Outcome rKL is constant, within tolerance.
[INFO 07-14 15:09:02] StandardizeY: Outcome JS is constant, within tolerance.
C:\Users\notes\Anaconda3\envs\grab\lib\site-packages

In [22]:
print(f"n_hidden: {deepensemble.n_hidden}")
print(f"dropout: {deepensemble.dropout}")

display(hyperopt_log(experiment))
hyperparam_plot(exp_model, "n_hidden", "dropout")

n_hidden: 91
dropout: 0.1


n_hidden   dropout        loss  fKL  rKL   JS
0         37  0.270325   10.106700  0.0  0.0  0.0
1         57  0.204090    9.557300  0.0  0.0  0.0
2         26  0.300268   10.122726  0.0  0.0  0.0
3         12  0.122308    9.262543  0.0  0.0  0.0
4         97  0.300804    9.656383  0.0  0.0  0.0
5         47  0.100000    9.352809  0.0  0.0  0.0
6          1  0.100000  113.098152  0.0  0.0  0.0
7         21  0.123602    9.399062  0.0  0.0  0.0
8         16  0.226290    9.663641  0.0  0.0  0.0
9         49  0.371325   10.314304  0.0  0.0  0.0
10        84  0.275587    9.633111  0.0  0.0  0.0
11        90  0.500000   10.349744  0.0  0.0  0.0
12        16  0.100000    9.377768  0.0  0.0  0.0
13        31  0.100000    9.404773  0.0  0.0  0.0
14        70  0.396949   10.160804  0.0  0.0  0.0
15        71  0.100000    9.344944  0.0  0.0  0.0
16        91  0.100000    9.253463  0.0  0.0  0.0
17        60  0.500000   10.952744  0.0  0.0  0.0
18        64  0.100000    9.344747  0.0  0.0  0.0
19        79  0.500000   10.639609  0.0  0.0  0.0
20       100  0.100000    9.265549  0.0  0.0  0.0
21        78  0.100000    9.335343  0.0  0.0  0.0
22        42  0.500000   11.299419  0.0  0.0  0.0
23        41  0.100000    9.364102  0.0  0.0  0.0
24       100  0.500000   10.352293  0.0  0.0  0.0
25        26  0.100000    9.383269  0.0  0.0  0.0
26        32  0.500000   11.450976  0.0  0.0  0.0
27        14  0.131730    9.399411  0.0  0.0  0.0
28        20  0.500000   10.997765  0.0  0.0  0.0
29        52  0.100000    9.347816  0.0  0.0  0.0

In [23]:
from performance.performance import prob_overlap, kl, js
p, q = prob_overlap(y, y_hat, bins=5)
print("fKL:", kl(p, q))
print("rKL:", kl(q, p))
print("JS:", js(p, q))

fKL: -0.23925831306205053
rKL: 0.33420208808667373
JS: 0.011813047399130097
